Reference: https://github.com/ShivamRajSharma/Transformer-Text-To-Speech



#Final model

##Imports

In [1]:
!pip install torchaudio
!pip install transformers

     |████████████████████████████████| 1.9MB 9.2MB/s 
     |████████████████████████████████| 2.3MB 8.5MB/s 
     |████████████████████████████████| 3.3MB 41.1MB/s 
     |████████████████████████████████| 901kB 45.5MB/s 


In [2]:
import os
import csv
import sys
import itertools
import numpy as np
import pandas as pd

In [3]:
import torch 
import torch.nn as nn 
from torch.nn.utils.rnn import pad_sequence

import pickle
from tqdm import tqdm 
from IPython.display import Audio 

import librosa
from librosa.feature import melspectrogram

In [4]:
import gc
import warnings
warnings.filterwarnings('ignore')

import torchaudio
import transformers
from sklearn.model_selection import train_test_split

##Download and filter dataset

### Downloads

In [ ]:
!rm -r /content/sample_data

#!wget https://github.com/ShivamRajSharma/Transformer-Text-To-Speech/blob/main/input/char_to_idx.pickle

In [ ]:
!git clone https://github.com/nii-yamagishilab/VCC2020-database.git

!rm -r /content/VCC2020-database/README
!rm -r /content/VCC2020-database/dbcl-10.txt
!rm -r /content/VCC2020-database/vcc2020_task_explanation.txt

Cloning into 'VCC2020-database'...
remote: Enumerating objects: 25, done.
remote: Counting objects: 100% (10/10), done.
remote: Compressing objects: 100% (10/10), done.
remote: Total 25 (delta 4), reused 0 (delta 0), pack-reused 15
Unpacking objects: 100% (25/25), done.


In [ ]:
!unzip /content/VCC2020-database/vcc2020_database_evaluation.zip -d /content/VCC2020-database
!rm -r /content/VCC2020-database/vcc2020_database_evaluation.zip
!unzip /content/VCC2020-database/vcc2020_database_groundtruth.zip -d /content/VCC2020-database
!rm -r /content/VCC2020-database/vcc2020_database_groundtruth.zip
!unzip /content/VCC2020-database/vcc2020_database_training_source.zip -d /content/VCC2020-database
!rm -r /content/VCC2020-database/vcc2020_database_training_source.zip
!unzip /content/VCC2020-database/vcc2020_database_training_target_task1.zip -d /content/VCC2020-database
!rm -r /content/VCC2020-database/vcc2020_database_training_target_task1.zip
!unzip /content/VCC2020-database/vcc2020_database_training_target_task2.zip -d /content/VCC2020-database
!rm -r /content/VCC2020-database/vcc2020_database_training_target_task2.zip
!unzip /content/VCC2020-database/vcc2020_database_transcriptions.zip -d /content/VCC2020-database
!rm -r /content/VCC2020-database/vcc2020_database_transcriptions.zip

!rm -r /content/VCC2020-database/__MACOSX
!mv /content/VCC2020-database/vcc2020_database_evaluation /content/VCC2020-database/test_source
!mv /content/VCC2020-database/vcc2020_database_groundtruth /content/VCC2020-database/test_target
!mv /content/VCC2020-database/vcc2020_database_transcriptions /content/VCC2020-database/transcriptions

Archive:  /content/VCC2020-database/vcc2020_database_evaluation.zip
   creating: /content/VCC2020-database/vcc2020_database_evaluation/
  inflating: /content/VCC2020-database/__MACOSX/._vcc2020_database_evaluation  
   creating: /content/VCC2020-database/vcc2020_database_evaluation/SEF2/
  inflating: /content/VCC2020-database/__MACOSX/vcc2020_database_evaluation/._SEF2  
  inflating: /content/VCC2020-database/vcc2020_database_evaluation/TeamInfo.txt  
  inflating: /content/VCC2020-database/__MACOSX/vcc2020_database_evaluation/._TeamInfo.txt  
   creating: /content/VCC2020-database/vcc2020_database_evaluation/SEM1/
  inflating: /content/VCC2020-database/__MACOSX/vcc2020_database_evaluation/._SEM1  
  inflating: /content/VCC2020-database/vcc2020_database_evaluation/README  
  inflating: /content/VCC2020-database/__MACOSX/vcc2020_database_evaluation/._README  
   creating: /content/VCC2020-database/vcc2020_database_evaluation/SEF1/
  inflating: /content/VCC2020-database/__MACOSX/vcc2020_d

###Data edits

In [ ]:
path = '/content/VCC2020-database'
data = os.listdir(path)
data.remove('.git')
data.remove('transcriptions')
data.sort()

for i in range(len(data)):
  data[i] = path+'/'+data[i]
  folder1=data[i]
  data[i] = os.listdir(folder1)
  data[i].sort()

  if 'dbcl-10.txt' in data[i]:
    data[i].remove('dbcl-10.txt')
  if '.DS_Store' in data[i]:
    data[i].remove('.DS_Store')
  if 'TeamInfo.txt' in data[i]:
    data[i].remove('TeamInfo.txt')
  if 'README' in data[i]:
    data[i].remove('README')

  for j in range(len(data[i])):
    data[i][j]=folder1+'/'+data[i][j]
    folder2=data[i][j]
    data[i][j] = os.listdir(folder2)
    data[i][j].sort()

    for k in range(len(data[i][j])):
      data[i][j][k]=folder2+'/'+data[i][j][k]
data = list(itertools.chain(*data))
data = list(itertools.chain(*data))

### delimiter

In [ ]:
#vcc2020_database_evaluation_transcriptions.txt
with open('/content/VCC2020-database/transcriptions/transcriptions_evaluation/vcc2020_database_evaluation_transcriptions.txt', 'r') as f:
    lines = f.readlines()
lines = ['E'+line[:5]+'|'+line[6:] for line in lines]
with open('/content/VCC2020-database/transcriptions/transcriptions_evaluation/vcc2020_database_evaluation_transcriptions.txt', 'w') as f:
    f.writelines(lines)

In [ ]:
#vcc2020_database_training_Eng_transcriptions.txt
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Eng_transcriptions.txt', 'r') as f:
    lines = f.readlines()
lines = ['E'+line[:5]+'|'+line[6:] for line in lines]
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Eng_transcriptions.txt', 'w') as f:
    f.writelines(lines)

In [ ]:
#vcc2020_database_training_Fin_transcriptions.txt
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Fin_transcriptions.txt', 'r') as f:
    lines = f.readlines()
lines = ['F'+line[:5]+'|'+line[6:] for line in lines]
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Fin_transcriptions.txt', 'w') as f:
    f.writelines(lines)

In [ ]:
#vcc2020_database_training_Ger_transcriptions.txt
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Ger_transcriptions.txt', 'r') as f:
    lines = f.readlines()
lines = ['G'+line[:5]+'|'+line[6:] for line in lines]
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Ger_transcriptions.txt', 'w') as f:
    f.writelines(lines)

In [ ]:
#vcc2020_database_training_Man_transcriptions.txt
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Man_transcriptions.txt', 'r') as f:
    lines = f.readlines()
lines = ['M'+line[:5]+'|'+line[6:] for line in lines]
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Man_transcriptions.txt', 'w') as f:
    f.writelines(lines)

### csv

In [ ]:
!mkdir /content/VCC2020-database/transcriptions/csv

In [ ]:
#eval
with open('/content/VCC2020-database/transcriptions/transcriptions_evaluation/vcc2020_database_evaluation_transcriptions.txt', 'r') as infile, open('/content/VCC2020-database/transcriptions/csv/vcc2020_database_evaluation_transcriptions.csv', 'w') as outfile:
  stripped = (line.strip() for line in infile)
  lines = (line.split("|") for line in stripped if line)
  writer = csv.writer(outfile)
  writer.writerows(lines)

In [ ]:
#eng
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Eng_transcriptions.txt', 'r') as infile, open('/content/VCC2020-database/transcriptions/csv/vcc2020_database_training_Eng_transcriptions.csv', 'w') as outfile:
  stripped = (line.strip() for line in infile)
  lines = (line.split("|") for line in stripped if line)
  writer = csv.writer(outfile)
  writer.writerows(lines)

In [ ]:
#fin
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Fin_transcriptions.txt', 'r') as infile, open('/content/VCC2020-database/transcriptions/csv/vcc2020_database_training_Fin_transcriptions.csv', 'w', encoding='utf-32') as outfile:
  stripped = (line.strip() for line in infile)
  lines = (line.split("|") for line in stripped if line)
  writer = csv.writer(outfile)
  writer.writerows(lines)

In [ ]:
#ger
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Ger_transcriptions.txt', 'r') as infile, open('/content/VCC2020-database/transcriptions/csv/vcc2020_database_training_Ger_transcriptions.csv', 'w', encoding='utf-32') as outfile:
  stripped = (line.strip() for line in infile)
  lines = (line.split("|") for line in stripped if line)
  writer = csv.writer(outfile)
  writer.writerows(lines)

In [ ]:
#man
with open('/content/VCC2020-database/transcriptions/transcriptions_training/vcc2020_database_training_Man_transcriptions.txt', 'r') as infile, open('/content/VCC2020-database/transcriptions/csv/vcc2020_database_training_Man_transcriptions.csv', 'w', encoding='utf-8-sig') as outfile:
  stripped = (line.strip() for line in infile)
  lines = (line.split("|") for line in stripped if line)
  writer = csv.writer(outfile)
  writer.writerows(lines)

### STT --not in use

In [ ]:
!pip install speechrecognition

     |████████████████████████████████| 32.8MB 90kB/s 


In [ ]:
import speech_recognition as sr
r = sr.Recognizer()
with sr.AudioFile('/content/VCC2020-database/source/SEF1/E10001.wav') as source:
    audio_text = r.listen(source)
    text = r.recognize_google(audio_text)
    print(text)

The Province I mentioned an insurmountable


##Source dataset

###1. SEF1

In [ ]:
data[0:70] #train

['/content/VCC2020-database/source/SEF1/E10001.wav',
 '/content/VCC2020-database/source/SEF1/E10002.wav',
 '/content/VCC2020-database/source/SEF1/E10003.wav',
 '/content/VCC2020-database/source/SEF1/E10004.wav',
 '/content/VCC2020-database/source/SEF1/E10005.wav',
 '/content/VCC2020-database/source/SEF1/E10006.wav',
 '/content/VCC2020-database/source/SEF1/E10007.wav',
 '/content/VCC2020-database/source/SEF1/E10008.wav',
 '/content/VCC2020-database/source/SEF1/E10009.wav',
 '/content/VCC2020-database/source/SEF1/E10010.wav',
 '/content/VCC2020-database/source/SEF1/E10011.wav',
 '/content/VCC2020-database/source/SEF1/E10012.wav',
 '/content/VCC2020-database/source/SEF1/E10013.wav',
 '/content/VCC2020-database/source/SEF1/E10014.wav',
 '/content/VCC2020-database/source/SEF1/E10015.wav',
 '/content/VCC2020-database/source/SEF1/E10016.wav',
 '/content/VCC2020-database/source/SEF1/E10017.wav',
 '/content/VCC2020-database/source/SEF1/E10018.wav',
 '/content/VCC2020-database/source/SEF1/E10019

In [ ]:
data[980:1005] #test

['/content/VCC2020-database/test_source/SEF1/E30001.wav',
 '/content/VCC2020-database/test_source/SEF1/E30002.wav',
 '/content/VCC2020-database/test_source/SEF1/E30003.wav',
 '/content/VCC2020-database/test_source/SEF1/E30004.wav',
 '/content/VCC2020-database/test_source/SEF1/E30005.wav',
 '/content/VCC2020-database/test_source/SEF1/E30006.wav',
 '/content/VCC2020-database/test_source/SEF1/E30007.wav',
 '/content/VCC2020-database/test_source/SEF1/E30008.wav',
 '/content/VCC2020-database/test_source/SEF1/E30009.wav',
 '/content/VCC2020-database/test_source/SEF1/E30010.wav',
 '/content/VCC2020-database/test_source/SEF1/E30011.wav',
 '/content/VCC2020-database/test_source/SEF1/E30012.wav',
 '/content/VCC2020-database/test_source/SEF1/E30013.wav',
 '/content/VCC2020-database/test_source/SEF1/E30014.wav',
 '/content/VCC2020-database/test_source/SEF1/E30015.wav',
 '/content/VCC2020-database/test_source/SEF1/E30016.wav',
 '/content/VCC2020-database/test_source/SEF1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_source/SEF1/E30001.wav', autoplay=True)

###2. SEF2

In [ ]:
data[70:140] #train

['/content/VCC2020-database/source/SEF2/E10001.wav',
 '/content/VCC2020-database/source/SEF2/E10002.wav',
 '/content/VCC2020-database/source/SEF2/E10003.wav',
 '/content/VCC2020-database/source/SEF2/E10004.wav',
 '/content/VCC2020-database/source/SEF2/E10005.wav',
 '/content/VCC2020-database/source/SEF2/E10006.wav',
 '/content/VCC2020-database/source/SEF2/E10007.wav',
 '/content/VCC2020-database/source/SEF2/E10008.wav',
 '/content/VCC2020-database/source/SEF2/E10009.wav',
 '/content/VCC2020-database/source/SEF2/E10010.wav',
 '/content/VCC2020-database/source/SEF2/E10011.wav',
 '/content/VCC2020-database/source/SEF2/E10012.wav',
 '/content/VCC2020-database/source/SEF2/E10013.wav',
 '/content/VCC2020-database/source/SEF2/E10014.wav',
 '/content/VCC2020-database/source/SEF2/E10015.wav',
 '/content/VCC2020-database/source/SEF2/E10016.wav',
 '/content/VCC2020-database/source/SEF2/E10017.wav',
 '/content/VCC2020-database/source/SEF2/E10018.wav',
 '/content/VCC2020-database/source/SEF2/E10019

In [ ]:
data[1005:1030] #test

['/content/VCC2020-database/test_source/SEF2/E30001.wav',
 '/content/VCC2020-database/test_source/SEF2/E30002.wav',
 '/content/VCC2020-database/test_source/SEF2/E30003.wav',
 '/content/VCC2020-database/test_source/SEF2/E30004.wav',
 '/content/VCC2020-database/test_source/SEF2/E30005.wav',
 '/content/VCC2020-database/test_source/SEF2/E30006.wav',
 '/content/VCC2020-database/test_source/SEF2/E30007.wav',
 '/content/VCC2020-database/test_source/SEF2/E30008.wav',
 '/content/VCC2020-database/test_source/SEF2/E30009.wav',
 '/content/VCC2020-database/test_source/SEF2/E30010.wav',
 '/content/VCC2020-database/test_source/SEF2/E30011.wav',
 '/content/VCC2020-database/test_source/SEF2/E30012.wav',
 '/content/VCC2020-database/test_source/SEF2/E30013.wav',
 '/content/VCC2020-database/test_source/SEF2/E30014.wav',
 '/content/VCC2020-database/test_source/SEF2/E30015.wav',
 '/content/VCC2020-database/test_source/SEF2/E30016.wav',
 '/content/VCC2020-database/test_source/SEF2/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_source/SEF2/E30001.wav', autoplay=True)

###3. SEM1

In [ ]:
data[140:210] #train

['/content/VCC2020-database/source/SEM1/E10001.wav',
 '/content/VCC2020-database/source/SEM1/E10002.wav',
 '/content/VCC2020-database/source/SEM1/E10003.wav',
 '/content/VCC2020-database/source/SEM1/E10004.wav',
 '/content/VCC2020-database/source/SEM1/E10005.wav',
 '/content/VCC2020-database/source/SEM1/E10006.wav',
 '/content/VCC2020-database/source/SEM1/E10007.wav',
 '/content/VCC2020-database/source/SEM1/E10008.wav',
 '/content/VCC2020-database/source/SEM1/E10009.wav',
 '/content/VCC2020-database/source/SEM1/E10010.wav',
 '/content/VCC2020-database/source/SEM1/E10011.wav',
 '/content/VCC2020-database/source/SEM1/E10012.wav',
 '/content/VCC2020-database/source/SEM1/E10013.wav',
 '/content/VCC2020-database/source/SEM1/E10014.wav',
 '/content/VCC2020-database/source/SEM1/E10015.wav',
 '/content/VCC2020-database/source/SEM1/E10016.wav',
 '/content/VCC2020-database/source/SEM1/E10017.wav',
 '/content/VCC2020-database/source/SEM1/E10018.wav',
 '/content/VCC2020-database/source/SEM1/E10019

In [ ]:
data[1030:1055] #test

['/content/VCC2020-database/test_source/SEM1/E30001.wav',
 '/content/VCC2020-database/test_source/SEM1/E30002.wav',
 '/content/VCC2020-database/test_source/SEM1/E30003.wav',
 '/content/VCC2020-database/test_source/SEM1/E30004.wav',
 '/content/VCC2020-database/test_source/SEM1/E30005.wav',
 '/content/VCC2020-database/test_source/SEM1/E30006.wav',
 '/content/VCC2020-database/test_source/SEM1/E30007.wav',
 '/content/VCC2020-database/test_source/SEM1/E30008.wav',
 '/content/VCC2020-database/test_source/SEM1/E30009.wav',
 '/content/VCC2020-database/test_source/SEM1/E30010.wav',
 '/content/VCC2020-database/test_source/SEM1/E30011.wav',
 '/content/VCC2020-database/test_source/SEM1/E30012.wav',
 '/content/VCC2020-database/test_source/SEM1/E30013.wav',
 '/content/VCC2020-database/test_source/SEM1/E30014.wav',
 '/content/VCC2020-database/test_source/SEM1/E30015.wav',
 '/content/VCC2020-database/test_source/SEM1/E30016.wav',
 '/content/VCC2020-database/test_source/SEM1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_source/SEM1/E30001.wav', autoplay=True)

###4. SEM2

In [ ]:
data[210:280] #train

['/content/VCC2020-database/source/SEM2/E10001.wav',
 '/content/VCC2020-database/source/SEM2/E10002.wav',
 '/content/VCC2020-database/source/SEM2/E10003.wav',
 '/content/VCC2020-database/source/SEM2/E10004.wav',
 '/content/VCC2020-database/source/SEM2/E10005.wav',
 '/content/VCC2020-database/source/SEM2/E10006.wav',
 '/content/VCC2020-database/source/SEM2/E10007.wav',
 '/content/VCC2020-database/source/SEM2/E10008.wav',
 '/content/VCC2020-database/source/SEM2/E10009.wav',
 '/content/VCC2020-database/source/SEM2/E10010.wav',
 '/content/VCC2020-database/source/SEM2/E10011.wav',
 '/content/VCC2020-database/source/SEM2/E10012.wav',
 '/content/VCC2020-database/source/SEM2/E10013.wav',
 '/content/VCC2020-database/source/SEM2/E10014.wav',
 '/content/VCC2020-database/source/SEM2/E10015.wav',
 '/content/VCC2020-database/source/SEM2/E10016.wav',
 '/content/VCC2020-database/source/SEM2/E10017.wav',
 '/content/VCC2020-database/source/SEM2/E10018.wav',
 '/content/VCC2020-database/source/SEM2/E10019

In [ ]:
data[1055:1080] #test

['/content/VCC2020-database/test_source/SEM2/E30001.wav',
 '/content/VCC2020-database/test_source/SEM2/E30002.wav',
 '/content/VCC2020-database/test_source/SEM2/E30003.wav',
 '/content/VCC2020-database/test_source/SEM2/E30004.wav',
 '/content/VCC2020-database/test_source/SEM2/E30005.wav',
 '/content/VCC2020-database/test_source/SEM2/E30006.wav',
 '/content/VCC2020-database/test_source/SEM2/E30007.wav',
 '/content/VCC2020-database/test_source/SEM2/E30008.wav',
 '/content/VCC2020-database/test_source/SEM2/E30009.wav',
 '/content/VCC2020-database/test_source/SEM2/E30010.wav',
 '/content/VCC2020-database/test_source/SEM2/E30011.wav',
 '/content/VCC2020-database/test_source/SEM2/E30012.wav',
 '/content/VCC2020-database/test_source/SEM2/E30013.wav',
 '/content/VCC2020-database/test_source/SEM2/E30014.wav',
 '/content/VCC2020-database/test_source/SEM2/E30015.wav',
 '/content/VCC2020-database/test_source/SEM2/E30016.wav',
 '/content/VCC2020-database/test_source/SEM2/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_source/SEM2/E30001.wav', autoplay=True)

##Target dataset

###1. TEF1

In [ ]:
data[280:350] #train

['/content/VCC2020-database/target_task1/TEF1/E10051.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10052.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10053.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10054.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10055.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10056.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10057.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10058.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10059.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10060.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10061.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10062.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10063.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10064.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10065.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10066.wav',
 '/content/VCC2020-database/target_task1/TEF1/E10067.wav

In [ ]:
data[1080:1105] #test

['/content/VCC2020-database/test_target/TEF1/E30001.wav',
 '/content/VCC2020-database/test_target/TEF1/E30002.wav',
 '/content/VCC2020-database/test_target/TEF1/E30003.wav',
 '/content/VCC2020-database/test_target/TEF1/E30004.wav',
 '/content/VCC2020-database/test_target/TEF1/E30005.wav',
 '/content/VCC2020-database/test_target/TEF1/E30006.wav',
 '/content/VCC2020-database/test_target/TEF1/E30007.wav',
 '/content/VCC2020-database/test_target/TEF1/E30008.wav',
 '/content/VCC2020-database/test_target/TEF1/E30009.wav',
 '/content/VCC2020-database/test_target/TEF1/E30010.wav',
 '/content/VCC2020-database/test_target/TEF1/E30011.wav',
 '/content/VCC2020-database/test_target/TEF1/E30012.wav',
 '/content/VCC2020-database/test_target/TEF1/E30013.wav',
 '/content/VCC2020-database/test_target/TEF1/E30014.wav',
 '/content/VCC2020-database/test_target/TEF1/E30015.wav',
 '/content/VCC2020-database/test_target/TEF1/E30016.wav',
 '/content/VCC2020-database/test_target/TEF1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TEF1/E30001.wav', autoplay=True)

###2. TEF2

In [ ]:
data[350:420] #train

['/content/VCC2020-database/target_task1/TEF2/E10051.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10052.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10053.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10054.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10055.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10056.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10057.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10058.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10059.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10060.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10061.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10062.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10063.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10064.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10065.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10066.wav',
 '/content/VCC2020-database/target_task1/TEF2/E10067.wav

In [ ]:
data[1105:1130] #test

['/content/VCC2020-database/test_target/TEF2/E30001.wav',
 '/content/VCC2020-database/test_target/TEF2/E30002.wav',
 '/content/VCC2020-database/test_target/TEF2/E30003.wav',
 '/content/VCC2020-database/test_target/TEF2/E30004.wav',
 '/content/VCC2020-database/test_target/TEF2/E30005.wav',
 '/content/VCC2020-database/test_target/TEF2/E30006.wav',
 '/content/VCC2020-database/test_target/TEF2/E30007.wav',
 '/content/VCC2020-database/test_target/TEF2/E30008.wav',
 '/content/VCC2020-database/test_target/TEF2/E30009.wav',
 '/content/VCC2020-database/test_target/TEF2/E30010.wav',
 '/content/VCC2020-database/test_target/TEF2/E30011.wav',
 '/content/VCC2020-database/test_target/TEF2/E30012.wav',
 '/content/VCC2020-database/test_target/TEF2/E30013.wav',
 '/content/VCC2020-database/test_target/TEF2/E30014.wav',
 '/content/VCC2020-database/test_target/TEF2/E30015.wav',
 '/content/VCC2020-database/test_target/TEF2/E30016.wav',
 '/content/VCC2020-database/test_target/TEF2/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TEF2/E30001.wav', autoplay=True)

###3. TEM1

In [ ]:
data[420:490] #train

['/content/VCC2020-database/target_task1/TEM1/E10051.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10052.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10053.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10054.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10055.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10056.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10057.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10058.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10059.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10060.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10061.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10062.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10063.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10064.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10065.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10066.wav',
 '/content/VCC2020-database/target_task1/TEM1/E10067.wav

In [ ]:
data[1130:1155] #test

['/content/VCC2020-database/test_target/TEM1/E30001.wav',
 '/content/VCC2020-database/test_target/TEM1/E30002.wav',
 '/content/VCC2020-database/test_target/TEM1/E30003.wav',
 '/content/VCC2020-database/test_target/TEM1/E30004.wav',
 '/content/VCC2020-database/test_target/TEM1/E30005.wav',
 '/content/VCC2020-database/test_target/TEM1/E30006.wav',
 '/content/VCC2020-database/test_target/TEM1/E30007.wav',
 '/content/VCC2020-database/test_target/TEM1/E30008.wav',
 '/content/VCC2020-database/test_target/TEM1/E30009.wav',
 '/content/VCC2020-database/test_target/TEM1/E30010.wav',
 '/content/VCC2020-database/test_target/TEM1/E30011.wav',
 '/content/VCC2020-database/test_target/TEM1/E30012.wav',
 '/content/VCC2020-database/test_target/TEM1/E30013.wav',
 '/content/VCC2020-database/test_target/TEM1/E30014.wav',
 '/content/VCC2020-database/test_target/TEM1/E30015.wav',
 '/content/VCC2020-database/test_target/TEM1/E30016.wav',
 '/content/VCC2020-database/test_target/TEM1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TEM1/E30001.wav', autoplay=True)

###4. TEM2

In [ ]:
data[490:560] #train

['/content/VCC2020-database/target_task1/TEM2/E10051.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10052.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10053.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10054.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10055.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10056.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10057.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10058.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10059.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10060.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10061.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10062.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10063.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10064.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10065.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10066.wav',
 '/content/VCC2020-database/target_task1/TEM2/E10067.wav

In [ ]:
data[1155:1180] #test

['/content/VCC2020-database/test_target/TEM2/E30001.wav',
 '/content/VCC2020-database/test_target/TEM2/E30002.wav',
 '/content/VCC2020-database/test_target/TEM2/E30003.wav',
 '/content/VCC2020-database/test_target/TEM2/E30004.wav',
 '/content/VCC2020-database/test_target/TEM2/E30005.wav',
 '/content/VCC2020-database/test_target/TEM2/E30006.wav',
 '/content/VCC2020-database/test_target/TEM2/E30007.wav',
 '/content/VCC2020-database/test_target/TEM2/E30008.wav',
 '/content/VCC2020-database/test_target/TEM2/E30009.wav',
 '/content/VCC2020-database/test_target/TEM2/E30010.wav',
 '/content/VCC2020-database/test_target/TEM2/E30011.wav',
 '/content/VCC2020-database/test_target/TEM2/E30012.wav',
 '/content/VCC2020-database/test_target/TEM2/E30013.wav',
 '/content/VCC2020-database/test_target/TEM2/E30014.wav',
 '/content/VCC2020-database/test_target/TEM2/E30015.wav',
 '/content/VCC2020-database/test_target/TEM2/E30016.wav',
 '/content/VCC2020-database/test_target/TEM2/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TEM2/E30001.wav', autoplay=True)

###5. TFF1

In [ ]:
data[560:630] #train

['/content/VCC2020-database/target_task2/TFF1/F10001.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10002.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10003.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10004.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10005.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10006.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10007.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10008.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10009.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10010.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10011.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10012.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10013.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10014.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10015.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10016.wav',
 '/content/VCC2020-database/target_task2/TFF1/F10017.wav

In [ ]:
data[1180:1205] #test

['/content/VCC2020-database/test_target/TFF1/E30001.wav',
 '/content/VCC2020-database/test_target/TFF1/E30002.wav',
 '/content/VCC2020-database/test_target/TFF1/E30003.wav',
 '/content/VCC2020-database/test_target/TFF1/E30004.wav',
 '/content/VCC2020-database/test_target/TFF1/E30005.wav',
 '/content/VCC2020-database/test_target/TFF1/E30006.wav',
 '/content/VCC2020-database/test_target/TFF1/E30007.wav',
 '/content/VCC2020-database/test_target/TFF1/E30008.wav',
 '/content/VCC2020-database/test_target/TFF1/E30009.wav',
 '/content/VCC2020-database/test_target/TFF1/E30010.wav',
 '/content/VCC2020-database/test_target/TFF1/E30011.wav',
 '/content/VCC2020-database/test_target/TFF1/E30012.wav',
 '/content/VCC2020-database/test_target/TFF1/E30013.wav',
 '/content/VCC2020-database/test_target/TFF1/E30014.wav',
 '/content/VCC2020-database/test_target/TFF1/E30015.wav',
 '/content/VCC2020-database/test_target/TFF1/E30016.wav',
 '/content/VCC2020-database/test_target/TFF1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TFF1/E30001.wav', autoplay=True)

###6. TFM1

In [ ]:
data[630:700] #train

['/content/VCC2020-database/target_task2/TFM1/F10001.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10002.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10003.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10004.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10005.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10006.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10007.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10008.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10009.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10010.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10011.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10012.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10013.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10014.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10015.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10016.wav',
 '/content/VCC2020-database/target_task2/TFM1/F10017.wav

In [ ]:
data[1205:1230] #test

['/content/VCC2020-database/test_target/TFM1/E30001.wav',
 '/content/VCC2020-database/test_target/TFM1/E30002.wav',
 '/content/VCC2020-database/test_target/TFM1/E30003.wav',
 '/content/VCC2020-database/test_target/TFM1/E30004.wav',
 '/content/VCC2020-database/test_target/TFM1/E30005.wav',
 '/content/VCC2020-database/test_target/TFM1/E30006.wav',
 '/content/VCC2020-database/test_target/TFM1/E30007.wav',
 '/content/VCC2020-database/test_target/TFM1/E30008.wav',
 '/content/VCC2020-database/test_target/TFM1/E30009.wav',
 '/content/VCC2020-database/test_target/TFM1/E30010.wav',
 '/content/VCC2020-database/test_target/TFM1/E30011.wav',
 '/content/VCC2020-database/test_target/TFM1/E30012.wav',
 '/content/VCC2020-database/test_target/TFM1/E30013.wav',
 '/content/VCC2020-database/test_target/TFM1/E30014.wav',
 '/content/VCC2020-database/test_target/TFM1/E30015.wav',
 '/content/VCC2020-database/test_target/TFM1/E30016.wav',
 '/content/VCC2020-database/test_target/TFM1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TFM1/E30001.wav', autoplay=True)

###7. TGF1

In [ ]:
data[700:770] #train

['/content/VCC2020-database/target_task2/TGF1/G10001.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10002.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10003.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10004.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10005.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10006.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10007.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10008.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10009.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10010.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10011.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10012.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10013.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10014.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10015.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10016.wav',
 '/content/VCC2020-database/target_task2/TGF1/G10017.wav

In [ ]:
data[1230:1255] #test

['/content/VCC2020-database/test_target/TGF1/E30001.wav',
 '/content/VCC2020-database/test_target/TGF1/E30002.wav',
 '/content/VCC2020-database/test_target/TGF1/E30003.wav',
 '/content/VCC2020-database/test_target/TGF1/E30004.wav',
 '/content/VCC2020-database/test_target/TGF1/E30005.wav',
 '/content/VCC2020-database/test_target/TGF1/E30006.wav',
 '/content/VCC2020-database/test_target/TGF1/E30007.wav',
 '/content/VCC2020-database/test_target/TGF1/E30008.wav',
 '/content/VCC2020-database/test_target/TGF1/E30009.wav',
 '/content/VCC2020-database/test_target/TGF1/E30010.wav',
 '/content/VCC2020-database/test_target/TGF1/E30011.wav',
 '/content/VCC2020-database/test_target/TGF1/E30012.wav',
 '/content/VCC2020-database/test_target/TGF1/E30013.wav',
 '/content/VCC2020-database/test_target/TGF1/E30014.wav',
 '/content/VCC2020-database/test_target/TGF1/E30015.wav',
 '/content/VCC2020-database/test_target/TGF1/E30016.wav',
 '/content/VCC2020-database/test_target/TGF1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TGF1/E30001.wav', autoplay=True)

###8. TGM1

In [ ]:
data[770:840] #train

['/content/VCC2020-database/target_task2/TGM1/G10001.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10002.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10003.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10004.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10005.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10006.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10007.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10008.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10009.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10010.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10011.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10012.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10013.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10014.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10015.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10016.wav',
 '/content/VCC2020-database/target_task2/TGM1/G10017.wav

In [ ]:
data[1255:1280] #test

['/content/VCC2020-database/test_target/TGM1/E30001.wav',
 '/content/VCC2020-database/test_target/TGM1/E30002.wav',
 '/content/VCC2020-database/test_target/TGM1/E30003.wav',
 '/content/VCC2020-database/test_target/TGM1/E30004.wav',
 '/content/VCC2020-database/test_target/TGM1/E30005.wav',
 '/content/VCC2020-database/test_target/TGM1/E30006.wav',
 '/content/VCC2020-database/test_target/TGM1/E30007.wav',
 '/content/VCC2020-database/test_target/TGM1/E30008.wav',
 '/content/VCC2020-database/test_target/TGM1/E30009.wav',
 '/content/VCC2020-database/test_target/TGM1/E30010.wav',
 '/content/VCC2020-database/test_target/TGM1/E30011.wav',
 '/content/VCC2020-database/test_target/TGM1/E30012.wav',
 '/content/VCC2020-database/test_target/TGM1/E30013.wav',
 '/content/VCC2020-database/test_target/TGM1/E30014.wav',
 '/content/VCC2020-database/test_target/TGM1/E30015.wav',
 '/content/VCC2020-database/test_target/TGM1/E30016.wav',
 '/content/VCC2020-database/test_target/TGM1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TGM1/E30001.wav', autoplay=True)

###9. TMF1

In [ ]:
data[840:910] #train

['/content/VCC2020-database/target_task2/TMF1/M10001.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10002.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10003.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10004.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10005.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10006.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10007.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10008.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10009.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10010.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10011.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10012.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10013.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10014.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10015.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10016.wav',
 '/content/VCC2020-database/target_task2/TMF1/M10017.wav

In [ ]:
data[1280:1305] #test

['/content/VCC2020-database/test_target/TMF1/E30001.wav',
 '/content/VCC2020-database/test_target/TMF1/E30002.wav',
 '/content/VCC2020-database/test_target/TMF1/E30003.wav',
 '/content/VCC2020-database/test_target/TMF1/E30004.wav',
 '/content/VCC2020-database/test_target/TMF1/E30005.wav',
 '/content/VCC2020-database/test_target/TMF1/E30006.wav',
 '/content/VCC2020-database/test_target/TMF1/E30007.wav',
 '/content/VCC2020-database/test_target/TMF1/E30008.wav',
 '/content/VCC2020-database/test_target/TMF1/E30009.wav',
 '/content/VCC2020-database/test_target/TMF1/E30010.wav',
 '/content/VCC2020-database/test_target/TMF1/E30011.wav',
 '/content/VCC2020-database/test_target/TMF1/E30012.wav',
 '/content/VCC2020-database/test_target/TMF1/E30013.wav',
 '/content/VCC2020-database/test_target/TMF1/E30014.wav',
 '/content/VCC2020-database/test_target/TMF1/E30015.wav',
 '/content/VCC2020-database/test_target/TMF1/E30016.wav',
 '/content/VCC2020-database/test_target/TMF1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TMF1/E30001.wav', autoplay=True)

###10. TMM1

In [ ]:
data[910:980] #train

['/content/VCC2020-database/target_task2/TMM1/M10001.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10002.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10003.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10004.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10005.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10006.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10007.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10008.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10009.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10010.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10011.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10012.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10013.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10014.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10015.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10016.wav',
 '/content/VCC2020-database/target_task2/TMM1/M10017.wav

In [ ]:
data[1305:1330] #test

['/content/VCC2020-database/test_target/TMM1/E30001.wav',
 '/content/VCC2020-database/test_target/TMM1/E30002.wav',
 '/content/VCC2020-database/test_target/TMM1/E30003.wav',
 '/content/VCC2020-database/test_target/TMM1/E30004.wav',
 '/content/VCC2020-database/test_target/TMM1/E30005.wav',
 '/content/VCC2020-database/test_target/TMM1/E30006.wav',
 '/content/VCC2020-database/test_target/TMM1/E30007.wav',
 '/content/VCC2020-database/test_target/TMM1/E30008.wav',
 '/content/VCC2020-database/test_target/TMM1/E30009.wav',
 '/content/VCC2020-database/test_target/TMM1/E30010.wav',
 '/content/VCC2020-database/test_target/TMM1/E30011.wav',
 '/content/VCC2020-database/test_target/TMM1/E30012.wav',
 '/content/VCC2020-database/test_target/TMM1/E30013.wav',
 '/content/VCC2020-database/test_target/TMM1/E30014.wav',
 '/content/VCC2020-database/test_target/TMM1/E30015.wav',
 '/content/VCC2020-database/test_target/TMM1/E30016.wav',
 '/content/VCC2020-database/test_target/TMM1/E30017.wav',
 '/content/VCC

In [ ]:
Audio('/content/VCC2020-database/test_target/TMM1/E30001.wav', autoplay=True)

## Code

###1. Configuration

In [ ]:
sample_rate=24000 #Provided in the paper
n_mels = 80
frame_rate = 80 #Provided in the paper
frame_length = 0.05
hop_length = int(sample_rate/frame_rate) 
win_length = int(sample_rate*frame_length)

scaling_factor = 4
min_db_level = -100

bce_weights = 7

embed_dims = 512
hidden_dims = 256 
heads = 4
forward_expansion = 4
num_layers = 4
dropout = 0.15
max_len = 1024
pad_idx = 0

Metadata = '/content/VCC2020-database/transcriptions/csv/vcc2020_database_evaluation_transcriptions.csv'
Audio_file_path = data[1130:1155]

Model_Path = './model.h5'
checkpoint = './checkpoint.bin'

Batch_Size = 2
Epochs = 40
LR = 3e-4
warmup_steps = 0.2

###2. Pickle upload

Upload the char2idx.pickle file from the git repo https://github.com/ShivamRajSharma/Transformer-Text-To-Speech
and load it accordingly. Here we had uploaded it on our drive

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
with open('/content/drive/MyDrive/char_to_idx.pickle', 'rb') as f:
    x = pickle.load(f)
    print(x)

{' ': 1, "'": 29, ',': 28, 'a': 2, 'b': 3, 'c': 4, 'd': 5, 'e': 6, 'f': 7, 'g': 8, 'h': 9, 'i': 10, 'j': 11, 'k': 12, 'l': 13, 'm': 14, 'n': 15, 'o': 16, 'p': 17, 'q': 18, 'r': 19, 's': 20, 't': 21, 'u': 22, 'v': 23, 'w': 24, 'x': 25, 'y': 26, 'z': 27, '.': 30}


###3. TTS

## Defining architecture of the TTS model

In [ ]:
class SelfAttention(nn.Module):
    def __init__(self, embed_dims, heads):
        super(SelfAttention, self).__init__()
        self.heads = heads
        self.embed_dims = embed_dims
        self.depth = embed_dims//heads
        self.query = nn.Linear(self.depth, self.depth)
        self.key = nn.Linear(self.depth, self.depth)
        self.value = nn.Linear(self.depth, self.depth)
        self.fc_out = nn.Linear(self.depth*self.heads*2, self.embed_dims)
    
    def forward(self, query, key, value, mask):
        batch, q_len, k_len, v_len = query.shape[0], query.shape[1], key.shape[1], value.shape[1]
        query = query.reshape(batch, q_len, self.heads, self.depth)
        key = key.reshape(batch, k_len, self.heads, self.depth)
        value = value.reshape(batch, v_len, self.heads, self.depth)
        query = self.query(query)
        key = self.key(key)
        value = self.value(value)
        energy = torch.einsum('bqhd, bkhd -> bhqk', [query, key])
        if mask is not None:
            energy.masked_fill(mask==0, float("-1e20"))
        energy =  torch.softmax((energy/((self.depth**1/2))), dim=-1)
        out = torch.einsum('bhqv, bvhd -> bqhd', [energy, value])
        out = out.reshape(batch, q_len, self.heads*self.depth)
        query = query.reshape(batch, q_len, self.heads*self.depth)
        out = torch.cat([query, out], dim=-1)
        out = self.fc_out(out)
        return out


class TransformerBlock(nn.Module):
    def __init__(self, hidden_dims, heads, dropout, forward_expansion):
        super(TransformerBlock, self).__init__()
        self.hidden_dims = hidden_dims
        self.heads = heads
        self.multihead_attention = SelfAttention(hidden_dims, heads)
        self.feed_forward = nn.Sequential(
            nn.Conv1d(hidden_dims, hidden_dims*forward_expansion, kernel_size=1),
            nn.GELU(),
            nn.Conv1d(hidden_dims*forward_expansion, hidden_dims, kernel_size=1))
        self.dropout = nn.Dropout(dropout)
        self.layer_norm1 = nn.LayerNorm(hidden_dims)
        self.layer_norm2 = nn.LayerNorm(hidden_dims)
    
    def forward(self, query, key, value, mask):
        attention_out = self.multihead_attention(query, key, value, mask)
        add = self.dropout(self.layer_norm1(attention_out + query))
        ffn_in = add.transpose(1, 2)
        ffn_out = self.feed_forward(ffn_in)
        ffn_out = ffn_out.transpose(1, 2)
        out = self.dropout(self.layer_norm2(ffn_out + add)) 
        return out


class EncoderPreNet(nn.Module):
    def __init__(self, embed_dims, hidden_dims, dropout):
        super(EncoderPreNet, self).__init__()
        self.conv1 = nn.Conv1d(
            embed_dims,
            hidden_dims,
            kernel_size=5, 
            padding=2)
        self.conv2 = nn.Conv1d(
            hidden_dims,
            hidden_dims,
            kernel_size=5, 
            padding=2)
        self.conv3 = nn.Conv1d(
            hidden_dims,
            hidden_dims,
            kernel_size=5, 
            padding=2)
        self.batch_norm1 = nn.BatchNorm1d(hidden_dims)
        self.batch_norm2 = nn.BatchNorm1d(hidden_dims)
        self.batch_norm3 = nn.BatchNorm1d(hidden_dims)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)
        self.dropout3 = nn.Dropout(dropout)
        self.fc_out = nn.Linear(hidden_dims, hidden_dims)
    
    def forward(self, x):
        x = x.transpose(1, 2)
        x = self.dropout1(torch.relu(self.batch_norm1(self.conv1(x))))
        x = self.dropout2(torch.relu(self.batch_norm2(self.conv2(x))))
        x = self.dropout3(torch.relu(self.batch_norm3(self.conv3(x))))
        x = x.transpose(1, 2)
        x = self.fc_out(x)
        return x


class Encoder(nn.Module):
    def __init__(
        self,hin
        vocab_size,
        embed_dims,
        hidden_dims,
        max_len,
        heads,
        forward_expansion,
        num_layers, 
        dropout):
        super(Encoder, self).__init__()
        self.token_embed = nn.Embedding(vocab_size, embed_dims)
        self.positional_embed = nn.Parameter(torch.zeros(1, max_len, hidden_dims))
        self.prenet = EncoderPreNet(embed_dims, hidden_dims, dropout)
        self.dropout = nn.Dropout(dropout)
        self.attention_layers = nn.Sequential(
            *[
                TransformerBlock(
                    hidden_dims, 
                    heads, 
                    dropout, 
                    forward_expansion
                )
                for _ in range(num_layers)
            ])
    
    def forward(self, x, mask=None):
        seq_len = x.shape[1]
        token_embed = self.token_embed(x)
        positional_embed = self.positional_embed[:, :seq_len, :]
        x = self.prenet(token_embed)
        x += positional_embed
        x = self.dropout(x)
        for layer in self.attention_layers:
            x = layer(x, x, x, mask)
        return x


class DecoderPreNet(nn.Module):
    def __init__(self, mel_dims, hidden_dims, dropout):
        super(DecoderPreNet, self).__init__()
        self.fc_out = nn.Sequential(
            nn.Linear(mel_dims, hidden_dims),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(hidden_dims, hidden_dims),
            nn.ReLU(),
            nn.Dropout(dropout))
    
    def forward(self, x):
        return self.fc_out(x)


class PostNet(nn.Module):
    def __init__(self, mel_dims, hidden_dims, dropout):
        #causal padding -> padding = (kernel_size - 1) x dilation
        #kernel_size = 5 -> padding = 4
        #Exclude the last padding_size output as we want only left padded output
        super(PostNet, self).__init__()
        self.conv1 = nn.Conv1d(mel_dims, hidden_dims, kernel_size=5, padding=4)
        self.batch_norm1 = nn.BatchNorm1d(hidden_dims)
        self.dropout1 = nn.Dropout(dropout)
        self.conv_list = nn.Sequential(
            *[
                nn.Conv1d(hidden_dims, hidden_dims, kernel_size=5, padding=4)
                for _ in range(3)
            ])
        self.batch_norm_list = nn.Sequential(
            *[
                nn.BatchNorm1d(hidden_dims)
                for _ in range(3)
            ])
        self.dropout_list = nn.Sequential(
            *[
                nn.Dropout(dropout)
                for _ in range(3)
            ])
        self.conv5 = nn.Conv1d(hidden_dims, mel_dims, kernel_size=5, padding=4)
    
    def forward(self, x):
        x = x.transpose(1, 2)
        x = self.dropout1(torch.tanh(self.batch_norm1(self.conv1(x)[:, :, :-4])))
        for dropout, batchnorm, conv in zip(self.dropout_list, self.batch_norm_list, self.conv_list):
            x = dropout(torch.tanh(batchnorm(conv(x)[:, :, :-4])))
        out = self.conv5(x)[:, :, :-4]
        out = out.transpose(1, 2)
        return out


class DecoderBlock(nn.Module):
    def __init__(
        self,
        embed_dims,
        heads,
        forward_expansion,
        dropout):
        super(DecoderBlock, self).__init__()
        self.causal_masked_attention = SelfAttention(embed_dims, heads)
        self.attention_layer = TransformerBlock(
            embed_dims, 
            heads, 
            dropout, 
            forward_expansion)
        self.dropout = nn.Dropout(dropout)
        self.layer_norm = nn.LayerNorm(embed_dims)
    
    def forward(self, query, key, value, src_mask, causal_mask):
        causal_masked_attention = self.causal_masked_attention(query, query, query, causal_mask)
        query = self.dropout(self.layer_norm(causal_masked_attention + query))
        out = self.attention_layer(query, key, value, src_mask)
        return out


class Decoder(nn.Module):
    def __init__(
        self,
        mel_dims,
        hidden_dims,
        heads,
        max_len,
        num_layers,
        forward_expansion,
        dropout):
        super(Decoder, self).__init__()
        self.positional_embed = nn.Parameter(torch.zeros(1, max_len, hidden_dims))
        self.prenet = DecoderPreNet(mel_dims, hidden_dims, dropout)
        self.attention_layers = nn.Sequential(
            *[
                DecoderBlock(
                    hidden_dims, 
                    heads, 
                    forward_expansion, 
                    dropout)
                for _  in range(num_layers)
            ])
        self.mel_linear = nn.Linear(hidden_dims, mel_dims)
        self.stop_linear = nn.Linear(hidden_dims, 1)
        self.postnet = PostNet(mel_dims, hidden_dims, dropout)
        self.dropout = nn.Dropout(dropout)
    
    def forward(self, mel, encoder_output, src_mask, casual_mask):
        seq_len = mel.shape[1]
        prenet_out = self.prenet(mel)
        x = self.dropout(prenet_out + self.positional_embed[:, :seq_len, :])
        for layer in self.attention_layers:
            x = layer(x, encoder_output, encoder_output, src_mask, casual_mask)
        stop_linear = self.stop_linear(x)
        mel_linear = self.mel_linear(x)
        postnet = self.postnet(mel_linear)
        out = postnet + mel_linear
        return out, mel_linear, stop_linear


class TransformerTTS(nn.Module):
    def __init__(
        self,
        vocab_size,
        embed_dims,
        hidden_dims, 
        heads,
        forward_expansion,
        num_layers,
        dropout,
        mel_dims,
        max_len,
        pad_idx):
        super(TransformerTTS, self).__init__()
        self.encoder = Encoder(
            vocab_size,
            embed_dims,
            hidden_dims,
            max_len,
            heads,
            forward_expansion,
            num_layers,
            dropout)
        
        self.decoder = Decoder(
            mel_dims,
            hidden_dims,
            heads,
            max_len,
            num_layers,
            forward_expansion,
            dropout)
        self.pad_idx = pad_idx

    def target_mask(self, mel, mel_mask):
        seq_len = mel.shape[1]
        pad_mask = (mel_mask != self.pad_idx).unsqueeze(1).unsqueeze(3)
        causal_mask = torch.tril(torch.ones((1, seq_len, seq_len))).unsqueeze(1)
        return pad_mask, causal_mask
    
    def input_mask(self, x):
        mask = (x != self.pad_idx).unsqueeze(1).unsqueeze(2)
        return mask
    
    def forward(self, text_idx, mel, mel_mask):
        input_pad_mask = self.input_mask(text_idx)
        target_pad_mask, causal_mask = self.target_mask(mel, mel_mask)
        encoder_out = self.encoder(text_idx, input_pad_mask)
        mel_postout, mel_linear, stop_linear = self.decoder(mel, encoder_out, target_pad_mask, causal_mask)
        return mel_postout, mel_linear, stop_linear

###4. Dataloader

In [ ]:
class TransformerLoader(torch.utils.data.Dataset):
    def __init__(self, files_name, text_data, mel_transforms=None, normalize=False):
        self.files_name = files_name
        self.text_data = text_data
        self.transforms = mel_transforms
        self.normalize = normalize
        self.char_to_idx = pickle.load(open('/content/drive/MyDrive/char_to_idx.pickle', 'rb'))
    
    def __len__(self):
        return len(self.text_data)
    
    def data_preprocess_(self, text):
        char_idx = [self.char_to_idx[char] for char in text if char in self.char_to_idx]
        return char_idx
    
    def normalize_(self, mel):
        #Normalizing data between -4 and 4 Converges even more faster
        mel = np.clip(
            (scaling_factor)*((mel - min_db_level)/-min_db_level) - scaling_factor, 
            -scaling_factor, scaling_factor)
        return mel

    def __getitem__(self, idx):
        num = int(idx/2)
        #print(int(idx/2), "sneha")
        #file_name = self.files_name[idx]
        text = self.text_data[idx]
        #print(text)
        text_idx = self.data_preprocess_(text)
        #print(text_idx)
        #audio_path = os.path.join(Audio_file_path + file_name + '.wav')
        #audio_file, _ = librosa.load(audio_path, sr=sample_rate)
        audio_file, _ = librosa.load(Audio_file_path[num], sr=sample_rate)
        audio_file, _ = librosa.effects.trim(audio_file)
        mel_spect = melspectrogram(
            audio_file,
            sr=sample_rate,
            n_mels=n_mels,
            hop_length=hop_length,
            win_length=win_length)
        pre_mel_spect = np.zeros((1, n_mels))
        mel_spect = librosa.power_to_db(mel_spect).T
        mel_spect = np.concatenate((pre_mel_spect, mel_spect), axis=0)
        if self.normalize:
            mel_spect = self.normalize_(mel_spect)
        mel_spect = torch.tensor(mel_spect, dtype=torch.float)
        mel_mask = [1]*mel_spect.shape[0]
        end_logits = [0]*(len(mel_spect) - 1)
        end_logits += [1]
        if self.transforms:
            for transform in self.transforms:
                if np.random.randint(0, 11) == 10:
                    mel_spect = transform(mel_spect).squeeze(0)
        return {
            'original_text'  : text,
            'mel_spect'     : mel_spect,
            'mel_mask'      : torch.tensor(mel_mask, dtype=torch.long),
            'text_idx'      : torch.tensor(text_idx, dtype=torch.long),
            'end_logits'    : torch.tensor(end_logits, dtype=torch.float)}


class MyCollate:
    def __init__(self, pad_idx, spect_pad):
        self.pad_idx = pad_idx
        self.spect_pad =spect_pad
    
    def __call__(self, batch):
        text_idx = [item['text_idx'] for item in batch]
        padded_text_idx = pad_sequence(
            text_idx,
            batch_first=True,
            padding_value=self.pad_idx)
        end_logits = [item['end_logits'] for item in batch]
        padded_end_logits  = pad_sequence(
            end_logits,
            batch_first=True,
            padding_value=0)
        original_text = [item['original_text'] for item in batch]
        mel_mask = [item['mel_mask'] for item in batch]
        padded_mel_mask = pad_sequence(
            mel_mask,
            batch_first=True,
            padding_value=0)
        mel_spects = [item['mel_spect'] for item in batch]
        batch_size, max_len = padded_mel_mask.shape
        padded_mel_spect = torch.zeros(batch_size, max_len, mel_spects[0].shape[-1])
        for num,mel_spect in enumerate(mel_spects):
            padded_mel_spect[num, :mel_spect.shape[0]] = mel_spect
        return {
            'original_text'  : original_text,
            'mel_spect'     : padded_mel_spect,
            'mel_mask'      : padded_mel_mask,
            'text_idx'      : padded_text_idx,
            'end_logits'    : padded_end_logits}

In [ ]:
def loss_fn(
    target_mel_spect, 
    target_end_logits, 
    pred_mel_spect_post, 
    pred_mel_spect, 
    pred_end_logits):
    mel_loss = nn.L1Loss()(pred_mel_spect, target_mel_spect) + nn.L1Loss()(pred_mel_spect_post, target_mel_spect)
    bce_loss = nn.BCEWithLogitsLoss(pos_weight=torch.tensor(bce_weights))(pred_end_logits.squeeze(-1), target_end_logits)
    return mel_loss + bce_loss

def train_fn(model, dataloader, optimizer, scheduler, device):
    running_loss = 0
    model.train()
    for num, data in tqdm(enumerate(dataloader), total=len(dataloader)):
        for p in model.parameters():
            p.grad=None
        end_logits = data['end_logits'].to(device)
        mel_spect = data['mel_spect'].to(device)
        text_idx = data['text_idx'].to(device)
        text = data['original_text']
        mel_mask = data['mel_mask'].to(device)
        mel_spect_post_pred, mel_spect_pred, end_logits_pred = model(text_idx, mel_spect[:, :-1], mel_mask[:, :-1])
        loss = loss_fn(
            mel_spect[:, 1:], 
            end_logits[:, :-1],
            mel_spect_post_pred,
            mel_spect_pred,
            end_logits_pred)
        running_loss += loss.item()
        loss.backward()
        optimizer.step()
        scheduler.step()
    epoch_loss = running_loss/len(dataloader)
    return epoch_loss

def eval_fn(model, dataloder, device):
    running_loss = 0
    model.eval()
    print("Type of model ",type(model))
    with torch.no_grad():
        for num, data in tqdm(enumerate(dataloder), total=len(dataloder)):
            end_logits = data['end_logits'].to(device)
            mel_spect = data['mel_spect'].to(device)
            text_idx = data['text_idx'].to(device)
            text = data['original_text']
            mel_mask = data['mel_mask'].to(device)
            mel_spect_post_pred, mel_spect_pred, end_logits_pred = model(text_idx, mel_spect[:, :-1], mel_mask[:, :-1])
            loss = loss_fn(
                mel_spect[:, 1:], 
                end_logits[:, :-1],
                mel_spect_post_pred,
                mel_spect_pred,
                end_logits_pred)   
            running_loss += loss.item()
    epoch_loss = running_loss/len(dataloder)
    return epoch_loss
'''
def test_fn(model, dataloder, device):
    # running_loss = 0
    features = []
    #model.eval()
    with torch.no_grad():
        for num, data in tqdm(enumerate(dataloder), total=len(dataloder)):
            end_logits = data['end_logits'].to(device)
            mel_spect = data['mel_spect'].to(device)
            text_idx = data['text_idx'].to(device)
            text = data['original_text']
            mel_mask = data['mel_mask'].to(device)
            mel_spect_post_pred, mel_spect_pred, end_logits_pred = model(text_idx, mel_spect[:, :-1], mel_mask[:, :-1])
            features.append((mel_spect_post_pred, mel_spect_pred, end_logits_pred))
    return features
'''
def test_fn(model, dataloder, device):
    running_loss = 0
    model.eval()
    with torch.no_grad():
        for num, data in tqdm(enumerate(dataloder), total=len(dataloder)):
            end_logits = data['end_logits'].to(device)
            mel_spect = data['mel_spect'].to(device)
            text_idx = data['text_idx'].to(device)
            text = data['original_text']
            mel_mask = data['mel_mask'].to(device)
            mel_spect_post_pred, mel_spect_pred, end_logits_pred = model(text_idx, mel_spect[:, :-1], mel_mask[:, :-1])
    return mel_spect

###5. Train

## Training the TTS model

In [ ]:
def preprocess(data):
    text_data, audio_files_name = [], []
    for d in data:
        #print(d)
        #audio_name, text = d.split('|')[:2]
        audio_name = d[:6]
        text = d[8:-1]
        text_data.append(text.lower())
        audio_files_name.append(audio_name)
    return text_data, audio_files_name

def train():
    data = open("/content/VCC2020-database/transcriptions/csv/vcc2020_database_evaluation_transcriptions.csv").read().strip().split('\n')[:10]
    text_data, audio_file_name = preprocess(data)
    print(text_data)
    print(len(text_data))
    del data
    gc.collect()
    transforms = [
        torchaudio.transforms.FrequencyMasking(freq_mask_param=15),
        torchaudio.transforms.TimeMasking(time_mask_param=35)]
    train_text_data, val_text_data, train_audio_file_name, val_audio_file_name = train_test_split(
        text_data, 
        audio_file_name, 
        test_size=0.2)
    train_data = TransformerLoader(
        files_name=train_audio_file_name,
        text_data=train_text_data,
        mel_transforms=transforms,
        normalize=True)
    print(val_audio_file_name)
    val_data = TransformerLoader(
        files_name=val_audio_file_name,
        text_data=val_text_data,
        normalize=True)
    pad_idx = 0
    train_loader = torch.utils.data.DataLoader(
        train_data,
        batch_size=Batch_Size,
        num_workers=1,
        pin_memory=True,
        collate_fn=MyCollate(
            pad_idx=pad_idx, 
            spect_pad=-scaling_factor))
    val_loader = torch.utils.data.DataLoader(
        val_data,
        batch_size=Batch_Size,
        num_workers=1,
        pin_memory=True,
        collate_fn=MyCollate(
            pad_idx=pad_idx, 
            spect_pad=-scaling_factor))
    vocab_size = len(train_data.char_to_idx) + 1
    model = TransformerTTS(
        vocab_size=vocab_size,
        embed_dims=embed_dims,
        hidden_dims=hidden_dims, 
        heads=heads,
        forward_expansion=forward_expansion,
        num_layers=num_layers,
        dropout=dropout,
        mel_dims=n_mels,
        max_len=max_len,
        pad_idx=pad_idx)
    device = torch.device('cpu')
    model = model.to(device)
    optimizer = transformers.AdamW(model.parameters(), lr=LR)
    num_training_steps = Epochs*len(train_data)//Batch_Size
    scheduler = transformers.get_cosine_schedule_with_warmup(
        optimizer,
        num_warmup_steps=warmup_steps*num_training_steps,
        num_training_steps=num_training_steps)
    epoch_start = 0
    checkpoint = './checkpoint.bin'
    if os.path.exists(checkpoint):
        checkpoint = torch.load(checkpoint)
        model.load_state_dict(checkpoint['model_state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        scheduler.load_state_dict(checkpoint['scheduler_state_dict'])
        epoch_start = checkpoint['epoch']
        print(f'---------[INFO] Restarting Training from Epoch {epoch_start} -----------\n')

    best_loss = 1e10 
    best_model = model.state_dict()
    print('--------- [INFO] STARTING TRAINING ---------\n')
    for epoch in range(epoch_start, Epochs):
        train_loss = train_fn(model, train_loader, optimizer, scheduler, device)
        val_loss = eval_fn(model, val_loader, device)
        print(f'EPOCH -> {epoch+1}/{Epochs} | TRAIN LOSS = {train_loss} | VAL LOSS = {val_loss} | LR = {scheduler.get_lr()[0]} \n')
        torch.save({
            'epoch'                 : epoch,
            'model_state_dict'      : model.state_dict(),
            'optimizer_state_dict'  : optimizer.state_dict(),
            'scheduler_state_dict'  : scheduler.state_dict(),
            'loss': val_loss,
            }, checkpoint)
        if best_loss > val_loss:
            best_loss = val_loss
            best_model = model
            torch.save(best_model, Model_Path)

train()

['in reality, the european parliament is practising delay tactics.', 'yoto must not remain an empty promise', ' emphatically reject such insinuations', 'trong forces are lined up against us', 'we are now facing a peculiar situation, really.', 'urkey must come to terms with the truth', 'the fishermen are inactive, tired and disappointed.', 'n recent years she has primarily appeared in television films such as little gloria', 'ismarck serves as a trade and shipping point for an area of large mechanized farms', 'uring the following years he tried unsuccessfully to get it into production']
10
['E30002', 'E30003']
--------- [INFO] STARTING TRAINING ---------



100%|██████████| 4/4 [00:02<00:00,  1.43it/s]

Type of model  <class '__main__.TransformerTTS'>



100%|██████████| 1/1 [00:00<00:00,  2.64it/s]


EPOCH -> 1/40 | TRAIN LOSS = 3.4074323773384094 | VAL LOSS = 2.819214344024658 | LR = 3.75e-05 



...

EPOCH -> 39/40 | TRAIN LOSS = 0.8268768787384033 | VAL LOSS = 0.6845811009407043 | LR = 7.222909991704773e-07 



100%|██████████| 4/4 [00:02<00:00,  1.41it/s]

Type of model  <class '__main__.TransformerTTS'>



100%|██████████| 1/1 [00:00<00:00,  2.68it/s]


EPOCH -> 40/40 | TRAIN LOSS = 0.8581408858299255 | VAL LOSS = 0.6861191987991333 | LR = 0.0 



###6. Test

This generates the Mel spectogram features for the vocoder to generate audio files. We used the output from this to feed into the espnet recipe for using vocoders and generating inferences

In [ ]:
test_text_data = ["This is good but not that great so that"]
test_data = TransformerLoader(
        files_name=None,
        text_data=test_text_data,
        normalize=True)
pad_idx = 0
test_loader = torch.utils.data.DataLoader(
        test_data,
        batch_size=Batch_Size,
        num_workers=1,
        pin_memory=True,
        collate_fn=MyCollate(
            pad_idx=pad_idx, 
            spect_pad=-scaling_factor))

vocab_size = len(test_data.char_to_idx) + 1
model = torch.load(Model_Path)
device = torch.device('cpu')
mel_spect = test_fn(model, test_loader, device)
mel_spect

100%|██████████| 1/1 [00:00<00:00,  4.13it/s]


tensor([[[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
         [-0.4150, -0.5780, -0.7584,  ..., -2.1863, -2.1863, -2.1863],
         [-0.4227, -0.7423, -0.8998,  ..., -2.1863, -2.1863, -2.1863],
         ...,
         [-0.6597, -0.8236, -0.9704,  ..., -2.1863, -2.1863, -2.1863],
         [-0.6740, -0.6339, -0.9520,  ..., -2.1863, -2.1863, -2.1863],
         [-0.4959, -0.6377, -0.8600,  ..., -2.1863, -2.1863, -2.1863]]])

In [ ]:
#np.array(mel_spect.tolist())[0].shape

(388, 80)

In [ ]:
#audio = librosa.feature.inverse.mel_to_audio(np.array(mel_spect.tolist())[0], sr=24000)
#audio.shape

(40448,)

In [6]:
#Audio(audio, rate=24000)
